In [40]:
import leidenalg
import igraph as ig
import numpy as np
import pandas as pd
import scanpy as sc

from collections import Counter

from ctxcore.genesig import GeneSignature 
from pyscenic.aucell import aucell, derive_auc_threshold, create_rankings
from sklearn.decomposition import PCA

In [41]:
##read in data

base_dir = "/u/home/j/jshin/scratch/medial_septum_sct/"
adata = sc.read(base_dir + "Saves/Supercells/AnnData/celltype_adata/Astrocyte.h5ad")
network = pd.read_csv(base_dir + "Saves/Supercells/AnnData/saved_networks/final_edges/Astrocyte.csv.gz")

In [42]:
adata

AnnData object with n_obs × n_vars = 13994 × 32285
    obs: 'sampleName', 'Genotype', 'SexChrom', 'Gonad', 'cell_type', 'Trisomy'
    var: 'vst.mean', 'vst.variance', 'vst.variance.expected', 'vst.variance.standardized', 'vst.variable'

In [43]:
#create and partition graph 
resolution_parameter = 0.0011 #idk what this is 
G = ig.Graph.TupleList([tuple(x) for x in network.values],
                       directed = True)

partition = leidenalg.find_partition(G, leidenalg.CPMVertexPartition, resolution_parameter = resolution_parameter);
groups = np.array(partition.membership)

In [87]:
#organizing gene membership dataframe
genes = G.vs['name']
gene_membership = pd.DataFrame(np.array([genes,groups]).T, columns = ['genes','cluster_membership'])
gene_membership = gene_membership.sort_values('genes')

In [45]:
# remove modules with 2 or fewer genes
group_count = Counter(gene_membership.cluster_membership)
groups_to_keep = []
for g in group_count:
    if group_count[g] > 2:
        groups_to_keep.append(g)
groups_to_keep = np.array(groups_to_keep)
gene_membership = gene_membership.loc[np.isin(gene_membership.cluster_membership,
                                              groups_to_keep)]

In [25]:
gene_membership.cluster_membership = gene_membership.cluster_membership.astype(str)

/tmp/ipykernel_32800/3844084652.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gene_membership.cluster_membership = gene_membership.cluster_membership.astype(str)


In [77]:
with open('test.gmt','w') as f:
    for tup in gene_membership.groupby(by='cluster_membership'):
        f.write(str(tup[0]+'\t'))
        for g in tup[1].genes:
            f.write(g+'\t')
        f.write('\n')

signatures = GeneSignature.from_gmt('test.gmt',
                                    field_separator='\t',
                                   gene_separator='\t')

In [79]:
gene_names = gene_membership.genes.values.ravel()

In [80]:
gene_names

array(['0610009B22Rik', '0610009E02Rik', '0610010K14Rik', ..., 'mt-Nd4',
       'mt-Nd4l', 'mt-Nd5'], dtype=object)

In [81]:
gene_names=gene_membership['genes'].tolist()

In [82]:
gene_names

['0610009B22Rik',
 '0610009E02Rik',
 '0610010K14Rik',
 '0610012G03Rik',
 '0610030E20Rik',
 '0610040B10Rik',
 '0610040F04Rik',
 '10',
 '100',
 '10000',
 '10001',
 '10002',
 '10003',
 '10004',
 '10005',
 '10006',
 '10007',
 '10008',
 '10009',
 '10010',
 '10011',
 '10012',
 '10013',
 '10014',
 '10015',
 '10016',
 '10018',
 '10021',
 '10022',
 '10025',
 '10027',
 '10028',
 '10029',
 '10031',
 '10036',
 '10037',
 '10039',
 '10040',
 '10041',
 '10042',
 '10043',
 '10047',
 '10048',
 '10055',
 '10056',
 '10057',
 '10058',
 '1006',
 '10060',
 '10061',
 '10062',
 '10065',
 '10066',
 '10068',
 '10069',
 '10070',
 '10071',
 '10072',
 '10073',
 '10074',
 '10075',
 '10076',
 '10077',
 '10078',
 '10080',
 '10081',
 '10083',
 '10084',
 '10085',
 '10087',
 '10088',
 '10089',
 '1009',
 '10090',
 '10091',
 '10093',
 '10094',
 '10095',
 '10096',
 '10097',
 '10098',
 '10099',
 '101',
 '1010',
 '10100',
 '10101',
 '10103',
 '10104',
 '10105',
 '10106',
 '10107',
 '10108',
 '10110',
 '10113',
 '10114',
 '10

In [59]:
adata[:, genes_keep]

KeyError: "Values ['10', '100', '10000', '10001', '10002', '10003', '10004', '10005', '10006', '10007', '10008', '10009', '10010', '10011', '10012', '10013', '10014', '10015', '10016', '10018', '10021', '10022', '10025', '10027', '10028', '10029', '10031', '10036', '10037', '10039', '10040', '10041', '10042', '10043', '10047', '10048', '10055', '10056', '10057', '10058', '1006', '10060', '10061', '10062', '10065', '10066', '10068', '10069', '10070', '10071', '10072', '10073', '10074', '10075', '10076', '10077', '10078', '10080', '10081', '10083', '10084', '10085', '10087', '10088', '10089', '1009', '10090', '10091', '10093', '10094', '10095', '10096', '10097', '10098', '10099', '101', '1010', '10100', '10101', '10103', '10104', '10105', '10106', '10107', '10108', '10110', '10113', '10114', '10116', '10117', '10118', '10119', '1012', '10120', '10121', '10123', '10124', '10126', '10127', '10128', '10129', '10130', '10131', '10132', '10133', '10134', '10135', '10136', '10137', '10138', '1

In [33]:
adata = adata[:,gene_membership.genes.values.ravel()]

KeyError: "Values ['10', '100', '10000', '10001', '10002', '10003', '10004', '10005', '10006', '10007', '10008', '10009', '10010', '10011', '10012', '10013', '10014', '10015', '10016', '10018', '10021', '10022', '10025', '10027', '10028', '10029', '10031', '10036', '10037', '10039', '10040', '10041', '10042', '10043', '10047', '10048', '10055', '10056', '10057', '10058', '1006', '10060', '10061', '10062', '10065', '10066', '10068', '10069', '10070', '10071', '10072', '10073', '10074', '10075', '10076', '10077', '10078', '10080', '10081', '10083', '10084', '10085', '10087', '10088', '10089', '1009', '10090', '10091', '10093', '10094', '10095', '10096', '10097', '10098', '10099', '101', '1010', '10100', '10101', '10103', '10104', '10105', '10106', '10107', '10108', '10110', '10113', '10114', '10116', '10117', '10118', '10119', '1012', '10120', '10121', '10123', '10124', '10126', '10127', '10128', '10129', '10130', '10131', '10132', '10133', '10134', '10135', '10136', '10137', '10138', '1

In [27]:
# test.gmt will need to be changed if doing this many times
# in parallel
with open('test.gmt','w') as f:
    for tup in gene_membership.groupby(by='cluster_membership'):
        f.write(str(tup[0]+'\t'))
        for g in tup[1].genes:
            f.write(g+'\t')
        f.write('\n')
        
signatures = GeneSignature.from_gmt('test.gmt',
                                    field_separator='\t',
                                   gene_separator='\t')

adata = adata[:,gene_membership.genes.values.ravel()]
sc.pp.normalize_total(adata, target_sum=1e4)
sc.pp.log1p(adata)
dge = pd.DataFrame(adata.X.T.todense())
dge.index = adata.var.index

KeyError: "Values ['10', '100', '10000', '10001', '10002', '10003', '10004', '10005', '10006', '10007', '10008', '10009', '10010', '10011', '10012', '10013', '10014', '10015', '10016', '10018', '10021', '10022', '10025', '10027', '10028', '10029', '10031', '10036', '10037', '10039', '10040', '10041', '10042', '10043', '10047', '10048', '10055', '10056', '10057', '10058', '1006', '10060', '10061', '10062', '10065', '10066', '10068', '10069', '10070', '10071', '10072', '10073', '10074', '10075', '10076', '10077', '10078', '10080', '10081', '10083', '10084', '10085', '10087', '10088', '10089', '1009', '10090', '10091', '10093', '10094', '10095', '10096', '10097', '10098', '10099', '101', '1010', '10100', '10101', '10103', '10104', '10105', '10106', '10107', '10108', '10110', '10113', '10114', '10116', '10117', '10118', '10119', '1012', '10120', '10121', '10123', '10124', '10126', '10127', '10128', '10129', '10130', '10131', '10132', '10133', '10134', '10135', '10136', '10137', '10138', '1